***<h1 style="text-align: center;">ETL pipeline using Kaggle, Databricks & Snowflake</h1>***

### Installation of Kaggle & Snowflake connector

In [0]:
%pip install kaggle
%pip install snowflake-connector-python

Python interpreter will be restarted.
  Created wheel for kaggle: filename=kaggle-1.5.16-py3-none-any.whl size=110699 sha256=3e97027b25b857b3a2426c3e1d1e701b298c14476090f7599c1d96854aef6ec9
  Stored in directory: /root/.cache/pip/wheels/d2/ed/a5/da3a0cfb13373d1ace41cafa4f2467d858c55c52473ba72799
Successfully built kaggle
Python interpreter will be restarted.
Python interpreter will be restarted.
  Attempting uninstall: cryptography
    Found existing installation: cryptography 3.4.8
    Not uninstalling cryptography at /databricks/python3/lib/python3.9/site-packages, outside environment /local_disk0/.ephemeral_nfs/envs/pythonEnv-f1286100-0d8b-404b-b1ec-64f05c3a90d1
    Can't uninstall 'cryptography'. No files were found to uninstall.
  Attempting uninstall: typing-extensions
    Found existing installation: typing-extensions 4.1.1
    Not uninstalling typing-extensions at /databricks/python3/lib/python3.9/site-packages, outside environment /local_disk0/.ephemeral_nfs/envs/pythonEnv-f12

### Function to setup Kaggle Authentication

In [0]:
import json
def kaggle_authentication(kaggle_auth, output_file):
    try:
        data = json.loads(kaggle_auth)
        with open(output_file, 'w') as file:
            json.dump(data, file, indent=4)
        print('successful authentication')
    except:
        print('authentication failed')

In [0]:
kaggle_authentication('{"username":"majdiakrmi","key":"3aa4b20c5ac5c0e1c8c82725d3cd3ffb"}', '/root/.kaggle/kaggle.json')

successful authentication


In [0]:
%sh
cat /root/.kaggle/kaggle.json

{
    "username": "majdiakrmi",
    "key": "3aa4b20c5ac5c0e1c8c82725d3cd3ffb"
}

### List Kaggle datasets

In [0]:
%sh kaggle datasets list

ref                                                        title                                         size  lastUpdated          downloadCount  voteCount  usabilityRating  
---------------------------------------------------------  -------------------------------------------  -----  -------------------  -------------  ---------  ---------------  
nelgiriyewithana/top-spotify-songs-2023                    Most Streamed Spotify Songs 2023              47KB  2023-08-26 11:04:57          12857        417  1.0              
joebeachcapital/students-performance                       Students Performance                           2KB  2023-08-31 00:50:11           4339        115  1.0              
carlmcbrideellis/zzzs-lightweight-training-dataset-target  Zzzs: Lightweight training dataset + target  185MB  2023-09-20 19:52:40            461         69  1.0              
iamsouravbanerjee/airline-dataset                          Airline Dataset                                8MB  2023-09-1

### Restrict the read permission of the file

In [0]:
%sh
chmod 600 /root/.kaggle/kaggle.json

## <span style="color:blue"> 1) Extract Data </span>

### Download Kaggle Dataset

In [0]:
%sh
kaggle datasets download -d sujaykapadnis/programming-languages


  0%|          | 0.00/859k [00:00<?, ?B/s]
100%|██████████| 859k/859k [00:00<00:00, 18.2MB/s]



### List download files

In [0]:
dbutils.fs.ls('file:/databricks/driver')

Out[55]: [FileInfo(path='file:/databricks/driver/azure/', name='azure/', size=4096, modificationTime=1695272205540),
 FileInfo(path='file:/databricks/driver/preload_class.lst', name='preload_class.lst', size=1306936, modificationTime=1695272205564),
 FileInfo(path='file:/databricks/driver/conf/', name='conf/', size=4096, modificationTime=1695272204968),
 FileInfo(path='file:/databricks/driver/hadoop_accessed_config.lst', name='hadoop_accessed_config.lst', size=2755, modificationTime=1695272205552),
 FileInfo(path='file:/databricks/driver/eventlogs/', name='eventlogs/', size=4096, modificationTime=1695318593829),
 FileInfo(path='file:/databricks/driver/root\\.kaggle\\kaggle.json', name='root\\.kaggle\\kaggle.json', size=79, modificationTime=1695324098873),
 FileInfo(path='file:/databricks/driver/metastore_db/', name='metastore_db/', size=4096, modificationTime=1695318919009),
 FileInfo(path='file:/databricks/driver/logs/', name='logs/', size=4096, modificationTime=1695326497776),
 FileI

### Unzip the files

In [0]:
%sh
unzip /databricks/driver/programming-languages.zip

Archive:  /databricks/driver/programming-languages.zip
  inflating: languages.csv           


In [0]:
dbutils.fs.ls('file:/databricks/driver/languages.csv')

Out[64]: [FileInfo(path='file:/databricks/driver/languages.csv', name='languages.csv', size=2618104, modificationTime=1694844548000)]

### Move unzipped files from driver mount to Filestore (Bronze Layer)

In [0]:
dbutils.fs.mv('file:/databricks/driver/languages.csv', 'dbfs:/FileStore/', recurse=True)

Out[65]: True

### List Filestore to see the moved files

In [0]:
dbutils.fs.ls('dbfs:/FileStore')

Out[68]: [FileInfo(path='dbfs:/FileStore/languages.csv', name='languages.csv', size=2618104, modificationTime=1695328536000),
 FileInfo(path='dbfs:/FileStore/shared_uploads/', name='shared_uploads/', size=0, modificationTime=0),
 FileInfo(path='dbfs:/FileStore/tables/', name='tables/', size=0, modificationTime=0)]

## <span style="color:blue"> 2) Transform Data </span>

### Spark Read CSV 

In [0]:
df = spark.read.csv('dbfs:/FileStore/languages.csv', header=True)

In [0]:
display(df)

pldb_id title description type appeared creators website domain_name domain_name_registered reference isbndb book_count semantic_scholar language_rank github_repo github_repo_stars github_repo_forks github_repo_updated github_repo_subscribers github_repo_created github_repo_description github_repo_issues github_repo_first_commit github_language github_language_tm_scope github_language_type github_language_ace_mode github_language_file_extensions github_language_repos wikipedia wikipedia_daily_page_views wikipedia_backlinks_count wikipedia_summary wikipedia_page_id wikipedia_appeared wikipedia_created wikipedia_revision_count wikipedia_related features_has_comments features_has_semantic_indentation features_has_line_comments line_comment_token last_activity number_of_users number_of_jobs origin_community central_package_repository_count file_type is_open_source java Java NA pl 1995 James Gosling https://oracle.com/java/ NA NA NA 400 401 37 0 NA NA NA NA NA NA NA NA NA Java source.java programming java java jav 11529980 https://en.wikipedia.org/wiki/Java_(programming_language) 5242 11543 "Java is a general-purpose computer programming language that is concurrent, class-based, object-oriented, and specifically designed to have as few implementation dependencies as possible. It is intended to let application developers ""write once run anywhere"" (WORA) meaning that compiled Java code can run on all platforms that support Java without the need for recompilation. Java applications are typically compiled to bytecode that can run on any Java virtual machine (JVM) regardless of computer architecture. As of 2016 Java is one of the most popular programming languages in use particularly for client-server web applications with a reported 9 million developers. Java was originally developed by James Gosling at Sun Microsystems (which has since been acquired by Oracle Corporation) and released in 1995 as a core component of Sun Microsystems' Java platform. The language derives much of its syntax from C and C++ but it has fewer low-level facilities than either of them. The original and reference implementation Java compilers virtual machines and class libraries were originally released by Sun under proprietary licenses. As of May 2007 in compliance with the specifications of the Java Community Process Sun relicensed most of its Java technologies under the GNU General Public License. Others have also developed alternative implementations of these Sun technologies such as the GNU Compiler for Java (bytecode compiler) GNU Classpath (standard libraries) and IcedTea-Web (browser plugin for applets). The latest version is Java 9 released on September 21 2017 and is one of the two versions currently supported for free by Oracle. Versions earlier than Java 8 are supported by companies on a commercial basis; e.g. by Oracle back to Java 6 as of October 2017 (while they still ""highly recommend that you uninstall"" pre-Java 8 from at least Windows computers)." javascript JavaScript NA pl 1995 Brendan Eich NA NA NA https://www.w3schools.com/js/js_reserved.asp 349 351 48 1 NA NA NA NA NA NA NA NA NA JavaScript source.js programming javascript js _js bones cjs es es6 frag gs jake javascript jsb jscad jsfl jslib jsm jspre jss jsx mjs njs pac sjs ssjs xsjs xsjslib 16046489 https://en.wikipedia.org/wiki/JavaScript 4264 8982 JavaScript (), often abbreviated as JS, is a high-level, dynamic, weakly typed, prototype-based, multi-paradigm, and interpreted programming language. Alongside HTML and CSS, JavaScript is one of the three core technologies of World Wide Web content production. It is used to make webpages interactive and provide online programs, including video games. The majority of websites employ it, and all modern web browsers support it without the need for plug-ins by means of a built-in JavaScript engine. Each of the many JavaScript engines represent a different implementation of JavaScript, all based on the ECMAScript specification, with some engin

In [0]:
df.count()

Out[71]: 4303

### Filter dataframe to collect Java title

In [0]:
c_df = df.filter(df.title.contains('C++'))
display(c_df)

pldb_id title description type appeared creators website domain_name domain_name_registered reference isbndb book_count semantic_scholar language_rank github_repo github_repo_stars github_repo_forks github_repo_updated github_repo_subscribers github_repo_created github_repo_description github_repo_issues github_repo_first_commit github_language github_language_tm_scope github_language_type github_language_ace_mode github_language_file_extensions github_language_repos wikipedia wikipedia_daily_page_views wikipedia_backlinks_count wikipedia_summary wikipedia_page_id wikipedia_appeared wikipedia_created wikipedia_revision_count wikipedia_related features_has_comments features_has_semantic_indentation features_has_line_comments line_comment_token last_activity number_of_users number_of_jobs origin_community central_package_repository_count file_type is_open_source cpp C++ NA pl 1985 Bjarne Stroustrup http://isocpp.org/ isocpp.org 2012 NA 128 128 6 6 NA NA NA NA NA NA NA NA NA C++ source.c++ programming c_cpp cpp c++ cc cp cxx h h++ hh hpp hxx inc inl ino ipp ixx re tcc tpp 2161625 https://en.wikipedia.org/wiki/C++ 4307 10943 C++ ( pronounced cee plus plus) is a general-purpose programming language. It has imperative, object-oriented and generic programming features, while also providing facilities for low-level memory manipulation. It was designed with a bias toward system programming and embedded, resource-constrained and large systems, with performance, efficiency and flexibility of use as its design highlights. C++ has also been found useful in many other contexts, with key strengths being software infrastructure and resource-constrained applications, including desktop applications, servers (e.g. e-commerce, web search or SQL servers), and performance-critical applications (e.g. telephone switches or space probes). C++ is a compiled language, with implementations of it available on many platforms. Many vendors provide C++ compilers, including the Free Software Foundation, Microsoft, Intel, and IBM. C++ is standardized by the International Organization for Standardization (ISO), with the latest standard version ratified and published by ISO in December 2014 as ISO/IEC 14882:2014 (informally known as C++14). The C++ programming language was initially standardized in 1998 as ISO/IEC 14882:1998, which was then amended by the C++03, ISO/IEC 14882:2003, standard. The current C++14 standard supersedes these and C++11, with new features and an enlarged standard library. Before the initial standardization in 1998, C++ was developed by Bjarne Stroustrup at Bell Labs since 1979, as an extension of the C language as he wanted an efficient and flexible language similar to C, which also provided high-level features for program organization. The C++17 standard is due in July 2017, with the draft largely implemented by some compilers already, and C++20 is the next planned standard thereafter. Many other programming languages have been influenced by C++, including C#, D, Java, and newer versions of C. 72038 1998 2001 1487 ada algol-68 c clu ml simula python csharp chapel d java lua perl php rust nim sql bcpl unix assembly-language regex NA NA NA // 2022 4128238 61098 Bell Labs 0 text NA objective-cpp Objective C++ Objective-C++ is simply source code that mixes Objective-C classes and C++ classes. pl 1993 NA NA NA NA https://en.wikipedia.org/wiki/Objective-C NA 0 NA 787 NA NA NA NA NA NA NA NA NA Objective-C++ source.objc++ programming objectivec mm 535669 NA NA NA NA NA NA NA NA NA TRUE FALSE TRUE // 2018 200 0 Apple 0 text NA micro-cpp ΜC++ NA pl 1992 pabuhr https://plg.uwaterloo.ca/usystem/uC++.html NA NA NA 0 0 0 1539 https://github.com/pabuhr/uCPP 133 26 2022 13 2013 concurrency for C++ 2 2013 NA NA NA NA NA NA https://en.wikipedia-on-ipfs.org/wiki/%CE%9CC%2B%2B 14 22 "μC++, also called uC++, is a programming language, an extension of C++ designed for concurrent programming. Among other features, it adds coroutines, tasks, and monitors, and

## <span style="color:blue"> 3) Load Data </span>

### Connection to Snowflake

In [0]:
snowOptions = {
    "sfURL" : "https://rpmrbue-yx05377.snowflakecomputing.com",
    "sfUser" : "MAJDIAKRMI",
    "sfPassword" : "Majdi@djo77",
    "sfDatabase" : "K_D_S_ETL",
    "sfSchema" : "LOAD_DATA",
    "sfWarehouse" : "COMPUTE_WH",
    "sfRole" : "accountadmin",
}

SNOWFLAKE_SOURCE_NAME = "net.snowflake.spark.snowflake"

### Write the dataframe to Snowflake

In [0]:
c_df.write \
    .format(SNOWFLAKE_SOURCE_NAME) \
    .options(**snowOptions) \
    .option("dbtable", "C_language") \
    .mode("overwrite") \
    .save()

***<h1 style="text-align: center;">End of the project</h1>***